In [3]:
# !pip install osmnx==1.3.0

In [4]:
# !pip install folium

In [5]:
# !pip install osmnx geopandas

In [6]:
import osmnx as ox
import osmnx.folium as ox_folium
import pandas as pd
import geopandas as gpd
import folium
import numpy as np
import networkx as nx
import random
from collections import deque
from shapely.geometry import Point, LineString
import matplotlib.colors as mcolors

In [7]:
place_name = "City of Westminster"

# networkx graph
graph = ox.graph_from_address(place_name, dist=1000)

# Plot the graph using folium
m = ox_folium.plot_graph_folium(graph)
m 

In [8]:
# CSV containing LSOA and MSOA codes
codes_df = pd.read_csv('Data/Code Lookup.csv', encoding="latin1", low_memory=False)

In [9]:
# Get all LSOA codes given MSOA name
msoa_name = "Westminster 018"
westminster_018_lsoas = codes_df[codes_df["msoa21nm"] == msoa_name]["lsoa21cd"].unique()

In [10]:
# Load the huge GeoJSON once (may take a while)
lsoa_gdf = gpd.read_file("Data/LSOA Boundaries 2021.geojson")

# Save it as a much faster binary format
lsoa_gdf.to_file("lsoas.gpkg", driver="GPKG")

In [11]:
# Filter for one LSOA
lsoa_code = "E01004763"
target_lsoa = lsoa_gdf[lsoa_gdf["LSOA21CD"] == lsoa_code]

# Ensure it's not empty
assert not target_lsoa.empty, "LSOA code not found."

# Extract and simplify the polygon
polygon = target_lsoa.geometry.values[0]
if polygon.geom_type == "MultiPolygon":
    polygon = max(polygon.geoms, key=lambda a: a.area)
polygon = polygon.simplify(0.001)

# Get the street network within the LSOA boundary
G = ox.graph_from_polygon(polygon, network_type="drive", simplify=True)

# Plot with folium
m = ox_folium.plot_graph_folium(G)
m

In [12]:
# Area map (not street view)
# Filter to only have the LSOAs in Westminster 018
subset = lsoa_gdf[lsoa_gdf["LSOA21CD"].isin(westminster_018_lsoas)]

# Get centroid to center the map
center = subset.unary_union.centroid.coords[:][0][::-1]  # (lat, lon)

# Create the folium map
m = folium.Map(location=center, zoom_start=15, tiles="cartodbpositron")

# Add the LSOA polygons
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "#3186cc",
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.4,
    },
    tooltip=folium.features.GeoJsonTooltip(fields=["LSOA21CD", "LSOA21NM"]),
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

m

C:\Users\20221219\AppData\Local\Temp\ipykernel_11816\7478970.py:6: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  center = subset.unary_union.centroid.coords[:][0][::-1]  # (lat, lon)


In [104]:
# Combine all LSOA geometries into one polygon
combined_polygon = subset.unary_union

# Simplify the geometry
simplified_polygon = combined_polygon.simplify(0.001)

# Step 2: Get the street network within that area
G = ox.graph_from_polygon(simplified_polygon, network_type="drive")

# Step 3: Convert graph to a folium map
map = ox.folium.plot_graph_folium(G, tiles="cartodbpositron")

# Optional: add LSOA boundary overlay
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "none",
        "color": "blue",
        "weight": 2,
    },
).add_to(map)

# Optional: Add layer control
folium.LayerControl().add_to(map)

# Step 4: Display map
map


C:\Users\20221219\AppData\Local\Temp\ipykernel_11816\812482050.py:2: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  combined_polygon = subset.unary_union


In [14]:
# This is to turn G into undirected graph
# G = G.to_undirected(reciprocal = False)

In [105]:
# save the nodes and edges into variables
nodes, edges = ox.graph_to_gdfs(G, nodes=True, edges=True)

In [106]:
edges["weight"] = 0

In [107]:
# Reset the index so 'osmid' becomes a column
edges = edges.reset_index()

# Confirm we now have u, v, key
required_columns = ['u', 'v', 'key']
if all(col in edges.columns for col in required_columns):
    edges = edges.set_index(required_columns)
else:
    raise ValueError(f"Missing one of the required columns: {required_columns}")

In [108]:
# Sample 20 random edges
sampled_edges = edges.sample(n=20, random_state=42)

# Generate random weights between 1 and 10
random_weights = np.random.randint(1, 11, size=20)

# Assign the weights directly to the GeoDataFrame
edges.loc[sampled_edges.index, "weight"] = random_weights

In [109]:
for index, row in edges.iterrows():
    edges.at[index, 'hot'] = 1 if row['weight'] > 5 else 0

In [110]:
# Sort the edges GeoDataFrame by 'weight' column in descending order
edges_sorted = edges.sort_values(by="weight", ascending=False)

# Display the top 10 edges with the highest weights
print(edges_sorted[['osmid', 'weight']].head(30))

                                                                  osmid  \
u          v          key                                                 
25257808   25257797   0                                         4253388   
1139318714 25504262   0                                       230503369   
25257291   25257298   0                                         4253454   
25257324   109631     0               [1067635384, 1067635385, 4370943]   
107798     107799     0                                         4356098   
361242661  25257815   0                                        86485148   
25257843   489796745  0                                       309458030   
256794572  2390005223 0                          [39093506, 1008674254]   
25257815   25257813   0                                       237702242   
9512922    26559655   0                                         4356104   
26846357   25496899   0                          [40412562, 1033673206]   
351771449  10574746   0  

In [111]:
# Check whether all edges in H exist in the graph
H = set(edges[edges['hot'] == 1].index)
missing_edges = [edge for edge in H if not G.has_edge(*edge)]

print(f"Missing edges: {missing_edges}")

Missing edges: []


In [112]:
hot_edges = edges[edges['hot'] == 1]
print(hot_edges[['weight']].describe())
print(hot_edges[hot_edges['weight'] > 0].shape)

          weight
count   9.000000
mean    8.333333
std     1.581139
min     6.000000
25%     7.000000
50%     9.000000
75%    10.000000
max    10.000000
(9, 17)


In [113]:
def find_unique_hot_routes(G, edges, nodes, k=5, m=1000, M=5000, max_iterations=1000):
    """
    Find unique routes with distinct starting segments.
    The first edge used is "hot".
    Route must be a cycle
    Uses directed graph G
    
    Parameters:
    - G: Original NetworkX graph
    - edges: GeoDataFrame with edge data
    - nodes: GeoDataFrame with node data
    - k: max routes to find
    - m: min route length
    - M: max route length
    - max_iterations: max attempts
    
    Returns:
    - List of (route, total_weight) tuples
    - working_G: The working graph
    """
    
    # Create working graph
    working_G = nx.DiGraph()
    for (u, v, key), row in edges.iterrows():
        length = row.get('length', 0)
        weight = row.get('weight', length)
        hot = row.get('hot', 0)
        
        working_G.add_edge(u, v, length=length, weight=weight, hot=hot, key=key)
        working_G.add_edge(v, u, length=length, weight=weight, hot=hot, key=key)
    
    routes_with_weights = []
    used_start_edges = set()
    iterations = 0
    
    # Get all hot edges once
    all_hot_edges = [
        (u, v) for u, v, data in working_G.edges(data=True)
        if data.get('hot', 0) == 1
    ]
    
    while (len(routes_with_weights) < k and 
           iterations < max_iterations and
           len(used_start_edges) < len(all_hot_edges)):
        
        iterations += 1
        
        # Get unused hot edges
        available_hot_edges = [
            edge for edge in all_hot_edges
            if edge not in used_start_edges
        ]
        
        if not available_hot_edges:
            break
            
        # Randomly select an unused starting edge
        # In next algorithm, can use hot edge with greatest weight as first edge of route
        start_edge = random.choice(available_hot_edges)
        start_node, next_node = start_edge
        
        # Initialize route tracking
        current_route = [start_node, next_node]
        current_length = working_G.edges[start_node, next_node]['length']
        current_weight = working_G.edges[start_node, next_node]['weight']
        visited_edges = {start_edge}
        
        # DFS stack: (node, route, length, weight, visited_edges)
        stack = deque([(next_node, current_route, current_length, current_weight, visited_edges)])
        
        found_route = None
        found_weight = 0
        
        while stack and not found_route:
            node, route, length, weight, visited = stack.pop()
            
            # Check if we can return to start
            if working_G.has_edge(node, start_node):
                return_edge = (node, start_node)
                if return_edge not in visited:
                    total_length = length + working_G.edges[node, start_node]['length']
                    total_weight = weight + working_G.edges[node, start_node]['weight']
                    
                    if m <= total_length <= M:
                        found_route = route + [start_node]
                        found_weight = total_weight
                        break
            
            # Skip if over max length
            if length > M:
                continue
                
            # Explore neighbors
            for neighbor in working_G.neighbors(node):
                edge = (node, neighbor)
                if edge not in visited:
                    edge_data = working_G.edges[node, neighbor]
                    new_length = length + edge_data['length']
                    new_weight = weight + edge_data['weight']
                    
                    if new_length <= M:
                        new_visited = visited.copy()
                        new_visited.add(edge)
                        stack.append((neighbor, route + [neighbor], new_length, new_weight, new_visited))
        
        if found_route:
            # Check for duplicate routes
            is_duplicate = any(
                route == found_route 
                for route, _ in routes_with_weights
            )
            
            if not is_duplicate:
                routes_with_weights.append((found_route, found_weight))
                used_start_edges.add(start_edge)
    
    return routes_with_weights, working_G

In [114]:
routes, working_G = find_unique_hot_routes(G, edges, nodes, k=5, m=800, M=3000)
i = 0
for route, weight in routes:
    print(f"Route {i+1}:")
    print(f"  Start edge: {route[0]}→{route[1]}")
    print(f"  Nodes: {route}")
    print(f"  Weight: {weight:.2f}")
    print(f"  Length: {sum(working_G.edges[route[i], route[i+1]]['length'] for i in range(len(route)-1)):.2f}m")
    i = i + 1

Route 1:
  Start edge: 25257324→109631
  Nodes: [25257324, 109631, 11707733694, 11707733695, 11707733696, 9789816, 11707733696, 6914171275, 11707733696, 11707733695, 2215490966, 11707733695, 11707733694, 109631, 25257324, 2910874877, 25257324, 108267, 25257324]
  Weight: 18.00
  Length: 863.56m
Route 2:
  Start edge: 489796745→25257843
  Nodes: [489796745, 25257843, 734894082, 25257843, 489796745, 2646395123, 734893873, 2646395125, 734894074, 2646395125, 734893873, 25257799, 311422051, 25257799, 25257797, 25257808, 1938450848, 25257808, 76465603, 881887804, 76465603, 2646395125, 76465603, 25257808, 6250236322, 25257815, 6250236322, 6250236321, 6250236322, 25257808, 25257797, 25257799, 734893873, 2646395123, 489796745]
  Weight: 34.00
  Length: 1730.81m
Route 3:
  Start edge: 361242661→25257815
  Nodes: [361242661, 25257815, 6250236322, 25257815, 361242661, 6250236319, 109577, 6250236319, 361242661]
  Weight: 14.00
  Length: 887.07m
Route 4:
  Start edge: 1139318714→25504262
  Nodes: [1

In [115]:
# Check if all nodes in your route exist in the graph
route1 = routes[0][0]
route2 = routes[1][0]
route3 = routes[2][0]
route4 = routes[3][0]
route5 = routes[4][0]
actual_routes = [route1, route2, route3, route4, route5]
missing_nodes = [node for node in route if node not in G.nodes]
print(f"Missing nodes: {missing_nodes}")

Missing nodes: []


In [116]:
# Combine all LSOA geometries into one polygon
combined_polygon = subset.unary_union

# Simplify the geometry
simplified_polygon = combined_polygon.simplify(0.001)

# Get the street network within that area
G = ox.graph_from_polygon(simplified_polygon, network_type="drive")

# Convert graph to a folium map
map = ox.folium.plot_graph_folium(G, tiles="cartodbpositron")

# Optional: add LSOA boundary overlay
folium.GeoJson(
    subset,
    name="Westminster 018 LSOAs",
    style_function=lambda x: {
        "fillColor": "none",
        "color": "blue",
        "weight": 2,
    },
).add_to(map)

# Weird with loop for some reason?
route_geoms1 = []
for u, v in zip(route1[:-1], route1[1:]):
    if G.has_edge(u, v):
        data = G.edges[u, v, 0]
    elif G.has_edge(v, u):
        data = G.edges[v, u, 0]
    else:
        print(f"Missing edge between {u} and {v}")
        continue
        
    if 'geometry' in data:
        route_geoms1.append(data['geometry'])
    else:
        # Create straight line if no geometry
        u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
        v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
        route_geoms1.append(LineString([u_pt, v_pt]))

if route_geoms1:
    gdf_route = gpd.GeoDataFrame(geometry=route_geoms1, crs="EPSG:4326")
    folium.GeoJson(
        gdf_route,
        name="Route 1",
        style_function=lambda x: {
            "color": "red",
            "weight": 5,
            "opacity": 1,
        }
    ).add_to(map)
    
route_geoms2 = []
for u, v in zip(route2[:-1], route2[1:]):
    if G.has_edge(u, v):
        data = G.edges[u, v, 0]
    elif G.has_edge(v, u):
        data = G.edges[v, u, 0]
    else:
        print(f"Missing edge between {u} and {v}")
        continue
        
    if 'geometry' in data:
        route_geoms2.append(data['geometry'])
    else:
        u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
        v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
        route_geoms2.append(LineString([u_pt, v_pt]))

if route_geoms2:
    gdf_route = gpd.GeoDataFrame(geometry=route_geoms2, crs="EPSG:4326")
    folium.GeoJson(
        gdf_route,
        name="Route 2",
        style_function=lambda x: {
            "color": "red",
            "weight": 5,
            "opacity": 1,
        }
    ).add_to(map)
    
route_geoms3 = []
for u, v in zip(route3[:-1], route3[1:]):
    if G.has_edge(u, v):
        data = G.edges[u, v, 0]
    elif G.has_edge(v, u):
        data = G.edges[v, u, 0]
    else:
        print(f"Missing edge between {u} and {v}")
        continue
        
    if 'geometry' in data:
        route_geoms3.append(data['geometry'])
    else:
        u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
        v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
        route_geoms3.append(LineString([u_pt, v_pt]))

if route_geoms3:
    gdf_route = gpd.GeoDataFrame(geometry=route_geoms3, crs="EPSG:4326")
    folium.GeoJson(
        gdf_route,
        name="Route 3",
        style_function=lambda x: {
            "color": "red",
            "weight": 5,
            "opacity": 1,
        }
    ).add_to(map)
    
route_geoms4 = []
for u, v in zip(route4[:-1], route4[1:]):
    if G.has_edge(u, v):
        data = G.edges[u, v, 0]
    elif G.has_edge(v, u):
        data = G.edges[v, u, 0]
    else:
        print(f"Missing edge between {u} and {v}")
        continue
        
    if 'geometry' in data:
        route_geoms4.append(data['geometry'])
    else:
        u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
        v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
        route_geoms4.append(LineString([u_pt, v_pt]))

if route_geoms4:
    gdf_route = gpd.GeoDataFrame(geometry=route_geoms4, crs="EPSG:4326")
    folium.GeoJson(
        gdf_route,
        name="Route 4",
        style_function=lambda x: {
            "color": "red",
            "weight": 5,
            "opacity": 1,
        }
    ).add_to(map)
    
route_geoms5 = []
for u, v in zip(route5[:-1], route5[1:]):
    if G.has_edge(u, v):
        data = G.edges[u, v, 0]
    elif G.has_edge(v, u):
        data = G.edges[v, u, 0]
    else:
        print(f"Missing edge between {u} and {v}")
        continue
        
    if 'geometry' in data:
        route_geoms5.append(data['geometry'])
    else:
        # Create straight line if no geometry
        u_pt = Point(G.nodes[u]['x'], G.nodes[u]['y'])
        v_pt = Point(G.nodes[v]['x'], G.nodes[v]['y'])
        route_geoms5.append(LineString([u_pt, v_pt]))

if route_geoms5:
    gdf_route = gpd.GeoDataFrame(geometry=route_geoms5, crs="EPSG:4326")
    folium.GeoJson(
        gdf_route,
        name="Route 5",
        style_function=lambda x: {
            "color": "red",
            "weight": 5,
            "opacity": 1,
        }
    ).add_to(map)
folium.LayerControl().add_to(map)

map

C:\Users\20221219\AppData\Local\Temp\ipykernel_11816\3171943685.py:2: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  combined_polygon = subset.unary_union


In [ ]:
map.save("Name It.html")